In [55]:
df_nes_learn.head()

sku  categoryLevel2Id  brandId                          userName  \
0  20005023           4010201      826  b2898a81b45310b30beb8fc0c0a9ce1e   
1  20020647           4030101     1425  538c73d64461e13907bb95c51c38bfbc   
2  20020701           4010401      124  ddca2d0101513a6209db7868eed8be05   
3  30012256           2030301       93  289c20015b3713a82ba5ddf774d996f7   
4  30011341           2050201      656  5576f82d149d4f688644fef2322c63ef   

   reting                                            comment commentNegative  \
0     2.0  2,5 года работала и все...устала! Лампочка гор...             NaN   
1     2.0  Через 2 месяца после истечении гарантийного ср...             NaN   
2     4.0  пользуюсь уже три недели. нареканий ни каких н...             NaN   
3     5.0  Ребят этот системный блок подойдёт для игры кс...             NaN   
4     5.0  я считаю, что яри замечательный телефон! Прият...             NaN   

  commentPositive  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN

In [10]:
import re
import nltk
from nltk.stem.porter import PorterStemmer

def get_tokens(stem):
    tokens = nltk.word_tokenize(stem)
    return tokens

def do_stemming(filtered):
    stemmed = []
    for f in filtered:
        stemmed.append(PorterStemmer().stem(f))  # не используется? снесите нах
    return stemmed

class Porter:
    PERFECTIVEGROUND =  re.compile(u"((ив|ивши|ившись|ыв|ывши|ывшись)|((?<=[ая])(в|вши|вшись)))$")
    REFLEXIVE = re.compile(u"(с[яь])$")
    ADJECTIVE = re.compile(u"(ее|ие|ые|ое|ими|ыми|ей|ий|ый|ой|ем|им|ым|ом|его|ого|ему|ому|их|ых|ую|юю|ая|яя|ою|ею)$")
    PARTICIPLE = re.compile(u"((ивш|ывш|ующ)|((?<=[ая])(ем|нн|вш|ющ|щ)))$")
    VERB = re.compile(u"((ила|ыла|ена|ейте|уйте|ите|или|ыли|ей|уй|ил|ыл|им|ым|ен|ило|ыло|ено|ят|ует|уют|ит|ыт|ены|ить|ыть|ишь|ую|ю)|((?<=[ая])(ла|на|ете|йте|ли|й|л|ем|н|ло|но|ет|ют|ны|ть|ешь|нно)))$")
    NOUN = re.compile(u"(а|ев|ов|ие|ье|е|иями|ями|ами|еи|ии|и|ией|ей|ой|ий|й|иям|ям|ием|ем|ам|ом|о|у|ах|иях|ях|ы|ь|ию|ью|ю|ия|ья|я)$")
    RVRE = re.compile(u"^(.*?[аеиоуыэюя])(.*)$")
    DERIVATIONAL = re.compile(u".*[^аеиоуыэюя]+[аеиоуыэюя].*ость?$")
    DER = re.compile(u"ость?$")
    SUPERLATIVE = re.compile(u"(ейше|ейш)$")
    I = re.compile(u"и$")
    P = re.compile(u"ь$")
    NN = re.compile(u"нн$")

    @staticmethod  # здесь не хватало staticmethod'а
    def stem(word):
        word = word.lower()
        word = word.replace(u'ё', u'е')
        m = re.match(Porter.RVRE, word)

        if m and m.groups():
            pre = m.group(1)
            rv = m.group(2)
            temp = Porter.PERFECTIVEGROUND.sub('', rv, 1)
            if temp != rv:
                rv = temp

            rv = Porter.REFLEXIVE.sub('', rv, 1)
            temp = Porter.ADJECTIVE.sub('', rv, 1)
            if temp != rv:
                rv = temp
                rv = Porter.PARTICIPLE.sub('', rv, 1)
            else:
                temp = Porter.VERB.sub('', rv, 1)
                if temp == rv:
                    rv = Porter.NOUN.sub('', rv, 1)
                else:
                    rv = temp

            rv = Porter.I.sub('', rv, 1)
            if re.match(Porter.DERIVATIONAL, rv):
                rv = Porter.DER.sub('', rv, 1)
                temp = Porter.P.sub('', rv, 1)
            if temp == rv:
                rv = Porter.SUPERLATIVE.sub('', rv, 1)
                rv = Porter.NN.sub(u'н', rv, 1)
            else:
                rv = temp
            word = pre+rv
        return word



# импортируем Pandas и Numpy
import re
import pandas as pd
import numpy as np
df = pd.read_csv('X_train.csv')
pd.set_option('display.max_columns', 20)
pd.set_option('display.max_rows', 1000)
cols = list(df.columns.values)

df_nes=df[['sku', 'categoryLevel2Id' , 'brandId', 'userName', 'reting' , 'comment' , 'commentNegative', 'commentPositive']]

#df_nes.head(n=100)
df_nes_learn=df_nes.head(n=10000)
df_nes_test=df_nes.tail(n=5550)
#df_nes_test.head()
#df_nes_learn.head()

for row in list(df_nes_learn.itertuples(index=True, name='Pandas')):
#for row in df_nes_learn.itertuples(index=True, name='Pandas'):
    tokens = get_tokens(getattr(row,'comment'))

    for token in tokens:
        if re.match(r'\w+', token):
            stemmed = Porter.stem(token)
            # print(token, '->', stemmed)
    # а можно сразу так:
    stems = [Porter.stem(token) for token in tokens if re.match(r'\w+', token)]
    print('оригинальный текст:')
    print(row.comment)
    print()
    print('стемы:')
    print(' '.join(stems))
    print('\n' + '-' * 60 + '\n')
    # print('                                      ')


оригинальный текст:
2,5 года работала и все...устала! Лампочка горит и больше ничего!

стемы:
2,5 года работа и все уста лампочка гор и больше нич

------------------------------------------------------------

оригинальный текст:
Через 2 месяца после истечении гарантийного срока машинка навернулась. Насчитали ремонту на 5500р! Причем брал её итальянской сборки!  Сама машинка была нормальная, правда после стирки снова прополаскивал, но это пожалуй про любую так скажешь - плохо выполаскивается порошок, хотя и сыплю/лью по инструкции и не фигню какую...  А мастер авторизованного сервис-центра поведал мне много интересного... Нет смысла переплачивать сегодня за европейскую страну изготовителя, нет смысла приобретать машинки дороже 12-15 тыс., и что сейчас все производители заведомо делают машинки, чтобы те ломались побыстрее ( в среднем раз в 3-4 года!!!) тем самым стимулируя спрос на новые... Единственное, что еще живо в отношении реального КАЧЕСТВА, так это пожалуй немецкое "Миеле" (Бош 

Раньше я кривился, думая о дороговизне PS 3, и решил купить X-Box, который сгорел через пол года, потом я купил PS 3 и ни о чем не жалею, эксклюзивы выходящие на PS 3 не только отличнейшие игры вообще, а ещё и одна из основных причин купить PS 3! Если вы любите игры или хотите сделать отличный подарок тому, кто любит игры, покупайте PlayStation 3 не задумываясь!

стемы:
раньше я крив дум о дороговизне ps 3 и реш куп x-box котор сгорел через пол года пот я куп ps 3 и ни о чем не жал эксклюзивы выходящ на ps 3 не только отличн игры вообще а еще и одна из основн причин куп ps 3 если вы люб игры или хот сдела отличн подарок тому кто люб игры покупа playstation 3 не задумыв

------------------------------------------------------------

оригинальный текст:
Супер приставка  Плохо одно диски дорогие

стемы:
супер приставка плохо одно диски дорог

------------------------------------------------------------

оригинальный текст:
Пылик подарили  в 2011 году. Для небольшой площади - 36 м2 - его на

оригинальный текст:
отличный ноутбук, хотя я и чайник, но как то быстро все настройки освоила без посторонней помощи, всё таки скорость и возможности его меня весьма порадовали. Дизайн весьма симпатичный, минус в быстром нагревании.

стемы:
отличн ноутбук хотя я и чайник но как то быстро все настройки осво без посторон помощи все таки скорость и возможн его меня весьма порадова дизайн весьма симпатичн минус в быстр нагревании

------------------------------------------------------------

оригинальный текст:
Каким участком головного мозга думал конструктор, оставив не металлическую резьбу на соединительные втулки.Коль так, надо вкладывать в комплектацию все необходимое для подключения.

стемы:
как участк головн мозга дума конструктор остав не металлическ резьбу на соединительн втулки.коль так надо вкладыва в комплектаци все необходим для подключения

------------------------------------------------------------

оригинальный текст:
купила недавно,  в использовании удобна - легко разбирае

Месяц назад приобрели данную модель и уже не в восторге от этой машинки.В отличие от предыдущей LG (которая прослужила верой и правдой в течении 8 лет), эта скачет как сумаcшедшая (транспортные болты удалены), грохот при отжиме стоит ужасный, в подъезде слышно даже, при отключении электроэнергии и вновь подключении сбрасывается на ноль цикл стирки (а не сохраняется в памяти).    В общем моя оценка такова: машинка не стоит тех денег и нервов.

стемы:
месяц назад приобрели дан модель и уже не в восторге от эт машинки.в отлич от предыдущ lg котор прослуж вер и правд в течении 8 лет эта скачет как сумаcшедш транспортн болты удал грохот при отжиме сто ужасн в подъезде слышно даже при отключении электроэнергии и вновь подключении сбрасыва на ноль цикл стирки а не сохраня в памяти в общ моя оценка такова машинка не сто тех денег и нервов

------------------------------------------------------------

оригинальный текст:
приобрела ,понравилось,не жалею.Доставка на дом через интернет магазин оче

Ноут свою цену оправдывает на 110%  После покупки сразу добавил 2Гб памяти. Появились проблемы, которые быстро решились прошивкой BIOS (прошивка есть на сайте Леновы). Батарея у ноута слабая, но к этой модели подходят аккумуляторы от Lenovo S9 и при желании можно купить 6 или даже 9-ячеечную батарею (4 и 6 часов работы соответственно).

стемы:
ноут сво цену оправдыва на 110 после покупки сразу добав 2гб памяти появ проблемы котор быстро реш прошивк bios прошивка есть на сайте леновы батарея у ноута слаб но к эт модели подход аккумуляторы от lenovo s9 и при желании можно куп 6 или даже 9-ячеечн батар 4 и 6 часов работы соответственно

------------------------------------------------------------

оригинальный текст:
Покупала из-за ножеточки. Ножи точит так себе, но сойдет, а открывалка - это что-то! очень удобно и быстро! больше нет порезаных пальцев, края банки загибаются хорошо да даже проткнуть банку прежде чем открыть иногда удается с трудом, а тут-ни забот, ни хлопот! очень довольна

...


оригинальный текст:
Плеер просто великолепный, видео форматы читает вобще круто, я даже кабельные каналы поймал, музыку слушать это просто класс, для меломанов подойдет.

стемы:
плеер просто великолепн видео форматы чита вобще круто я даже кабельн каналы пойма музыку слуша это просто класс для меломанов подойдет

------------------------------------------------------------

оригинальный текст:
Утюг отличный, долго выбирала, теперь жалею, что столько времени мучилась и не покупала. Гладит замечательно, очень длинный шнур, теперь не нужны переноски.

стемы:
утюг отличн долго выбира теперь жал что столько времени муч и не покупа глад замечательно очень длин шнур теперь не нужны переноски

------------------------------------------------------------

оригинальный текст:
Много читали в нете перед покупкой, какой лучше, пришли к выводу что по цене и качеству его собрат самсунг 4330. А когда пришли в магазин обнаружили вот этот самсунг 4350, он такой же, но с турбощеткой и немного мощнее! а 

оригинальный текст:
Единственный минус это непонятная работа вентилятора при включении особенно в мороз -25, как-то странно он жужжит.  Глюкнуло только пару раз, станции автоматически находит и переключается на них, когда с флешки например музыка играет, из-за чего так происходит непонятно.  gps не подключишь, ибо непредусмотренно конструкцией!

стемы:
единствен минус это непонятн работа вентилятора при включении особенно в мороз как-то странно он жужж глюкнуло только пару раз станции автоматически наход и переключа на них когда с флешки например музыка игра из-за чего так происход непонятно gps не подключ ибо непредусмотренно конструкци

------------------------------------------------------------

оригинальный текст:
Ноутбук замечательный для работы, но один минус нет микрофона.

стемы:
ноутбук замечательн для работы но один минус нет микрофона

------------------------------------------------------------

оригинальный текст:
Тут все о кисточках, да о кисточках, а я покупала выпрямит

Отличный нетбук!  Единственный в данном классе у кого память расширяется до 3 Гб. Сразу после покупки купил модуль на 2 Гб, теперь стоит максимум, что поддерживает WinXP    Видео в формате HD воспроизводит без всяких тормозов. Яркость и насыщенность цветов экрана просто на высоте.    Кроме того, в отличии от одноклассников, поддерживает блютус.    Очень лёгкий. Клавиатура стандартного размера, кнопки не уменьшены как у 10-дюймовых моделей.    Лучшего нетбука за эту цену не найти. Работаю 3 месяца - ненарадуюсь.

стемы:
отличн нетбук единствен в дан классе у кого памя расширя до 3 гб сразу после покупки куп модуль на 2 гб теперь сто максимум что поддержива winxp видео в формате hd воспроизвод без всяк тормозов яркость и насыщен цветов экра просто на высоте кроме того в отличии от одноклассников поддержива блютус очень легк клавиатура стандартн размера кнопки не уменьш как у 10-дюймов модел лучш нетбука за эту цену не найти работа 3 месяца ненарад

---------------------------------------

куп за поломк предыдущ наушников отход прав ухо.ц небольш скуп на это честно понрав упаковка вот и взял выглядело интересно когда опробова был в бешенстве от них звук никак все шип и также отход прав ухо дума ну все выкину щас их пот случайно встав в телефон и удив все отлично оказыва была проблема в плеере d поэт для их цены вроде нормальн ну быва и лучше

------------------------------------------------------------

оригинальный текст:
Телевизор приобрел несколько месяцев назад.   Недостатков в функционале не вижу. Немного неудобный пульт (громоздкая клавиша меню, которая так и норовит нажаться).  В целом вполне достойная покупка.  Огорчил правда тот факт, что указанные в описании функции "Картинка в картинке" и "Картинка и картинка" отсутствуют!

стемы:
телевизор приобрел несколько месяцев назад недостатков в функционале не вижу немн неудобн пульт громоздк клавиша мен котор так и норов нажа в цел вполне достойн покупка огорч правда тот факт что указанн в описании функции картинка в 

оригинальный текст:
Отличный телевизор для HD-ready, купил дочке в комнату, с расстояния 2-х метров картинка идеальная, единственный недостаток угол обзора по вертикали: если уровень глаз будет ниже нижнего края телевизора, то картинка становиться темной (чем ниже тем темнее), потому подвесил на стену нижний край телевизора чуть ниже уровня глаз и наклонил вперед на угол 7 градусов - в итоге с любого места, даже с пола картинка смотрится идеально. По функционалу удовлетворяет полностью, это уже второй филипс в нашей семье, первый 37" FullHD приютился в зале. Вообще эта серия радует - хорошее качество за приемлемые деньги. Следующий будет LED, когда подешевеет.

стемы:
отличн телевизор для hd-ready куп дочке в комнату с расстояния 2-х метров картинка идеальн единствен недостаток угол обзора по вертика если уровень глаз будет ниже нижн края телевизора то картинка станов темн чем ниже тем темн пот подвес на стену нижн край телевизора чуть ниже уровня глаз и наклон вперед на угол 7 градусо

In [56]:
df_nes_test.head()

sku  categoryLevel2Id  brandId                          userName  \
10037  20023434           4050301       64  33b67031842d4c56d9dc03571081b77d   
10038  20021798           4110104       10  fc7d8d59ae565bbc0d43d6a24d0f888f   
10039  20021697           4110102       80  6421219d872c945f8aa9dc434c923394   
10040  11023744           1070908       13  3d801da09e7d82668e226799d9db91dc   
10041  40054798           3030501     1542  560e1a279bae50a0248e626224828b4f   

       reting                                            comment  \
10037     5.0  Покупкой доволен,прежде чем купить изучал инос...   
10038     5.0              Пылесос просто супер. очень довольны!   
10039     5.0  Пользуюсь месяц и не вижу ни каких проблем. Мо...   
10040     2.0  Купил я этот телевизор Маме на день рождение. ...   
10041     5.0  Лучшего симулятора я ещё не встречал. Хорошая ...   

      commentNegative commentPositive  
10037             NaN             NaN  
10038             NaN             NaN  
10039             NaN             NaN  
10040             NaN             NaN  
10041             NaN             NaN

In [83]:
import nltk
from nltk.stem.porter import PorterStemmer



def get_tokens(stem):
    tokens = nltk.word_tokenize(stem)
    return tokens

def do_stemming(filtered):
    stemmed = []
    for f in filtered:
        stemmed.append(PorterStemmer().stem(f))
    return stemmed




In [117]:
class Porter:
	PERFECTIVEGROUND =  re.compile(u"((ив|ивши|ившись|ыв|ывши|ывшись)|((?<=[ая])(в|вши|вшись)))$")
	REFLEXIVE = re.compile(u"(с[яь])$")
	ADJECTIVE = re.compile(u"(ее|ие|ые|ое|ими|ыми|ей|ий|ый|ой|ем|им|ым|ом|его|ого|ему|ому|их|ых|ую|юю|ая|яя|ою|ею)$")
	PARTICIPLE = re.compile(u"((ивш|ывш|ующ)|((?<=[ая])(ем|нн|вш|ющ|щ)))$")
	VERB = re.compile(u"((ила|ыла|ена|ейте|уйте|ите|или|ыли|ей|уй|ил|ыл|им|ым|ен|ило|ыло|ено|ят|ует|уют|ит|ыт|ены|ить|ыть|ишь|ую|ю)|((?<=[ая])(ла|на|ете|йте|ли|й|л|ем|н|ло|но|ет|ют|ны|ть|ешь|нно)))$")
	NOUN = re.compile(u"(а|ев|ов|ие|ье|е|иями|ями|ами|еи|ии|и|ией|ей|ой|ий|й|иям|ям|ием|ем|ам|ом|о|у|ах|иях|ях|ы|ь|ию|ью|ю|ия|ья|я)$")
	RVRE = re.compile(u"^(.*?[аеиоуыэюя])(.*)$")
	DERIVATIONAL = re.compile(u".*[^аеиоуыэюя]+[аеиоуыэюя].*ость?$")
	DER = re.compile(u"ость?$")
	SUPERLATIVE = re.compile(u"(ейше|ейш)$")
	I = re.compile(u"и$")
	P = re.compile(u"ь$")
	NN = re.compile(u"нн$")

	def stem(word):
		word = word.lower()
		word = word.replace(u'ё', u'е')
		m = re.match(Porter.RVRE, word)
		if m.groups():
			pre = m.group(1)
			rv = m.group(2)
			temp = Porter.PERFECTIVEGROUND.sub('', rv, 1)
			if temp == rv:
				rv = Porter.REFLEXIVE.sub('', rv, 1)
				temp = Porter.ADJECTIVE.sub('', rv, 1)
				if temp != rv:
					rv = temp
					rv = Porter.PARTICIPLE.sub('', rv, 1)
				else:
					temp = Porter.VERB.sub('', rv, 1)
					if temp == rv:
						rv = Porter.NOUN.sub('', rv, 1)
					else:
						rv = temp
			else:
				rv = temp
			
			rv = Porter.I.sub('', rv, 1)

			if re.match(Porter.DERIVATIONAL, rv):
				rv = Porter.DER.sub('', rv, 1)

			temp = Porter.P.sub('', rv, 1)
			if temp == rv:
				rv = Porter.SUPERLATIVE.sub('', rv, 1)
				rv = Porter.NN.sub(u'н', rv, 1)
			else:
				rv = temp
			word = pre+rv
		return word